# TriScale Interactive Plots

This notebook generates and displays all the plots from the TriScale paper.

- [Figure 1.a](#Figure-1a)
- [Figure 1.b](#Figure-1b)
- [Figure 3.a](#Figure-3a)
- [Figure 3.b](#Figure-3b)
- [Figure 3.c](#Figure-3c)
- [Figure 4](#Figure-4)
- [Figure 5](#Figure-5)
- [Figure 6](#Figure-6)

---

In [1]:
# Necessary import

from pathlib import Path
import json
import yaml
import numpy as np
import pandas as pd

import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "notebook"

import triscale
import triplots
import UseCase_Pantheon.pantheon as pantheon

%load_ext autoreload
%autoreload 2

### Figure 1a

In [2]:
# Code that generate figure 1a
#
# ...

> **Figure 1 (a)** Data analysis and visualization reproduced from [[66]](). The dots represent the mean performance of the runs; the ellipses represent the $(1-\sigma)$ variation across runs.

[Back to top](#TriScale-Interactive-Plots)

### Figure 1b

In [3]:
# Code that generate figure 1b
#
# ...

> **Figure 1 (b)** Data analysis and visualization produced by _TriScale_. Dots represent the KPIs of each schemes. Shaded areas represent dominance regions: _scheme $A$_ is "strictly better" than _scheme $B$_if the KPI of $B$ strictly lies in the dominance region of $A$.

[Back to top](#TriScale-Interactive-Plots)

### Figure 3a

In [4]:
# Construct the path to the different test results
result_dir_path = Path('UseCase_Pantheon/PantheonData/10runs_30s')
result_dir_list = [x for x in result_dir_path.iterdir() if x.is_dir()]
# Meta data file name
meta_data_file  = 'pantheon_metadata.json'
# Config file name and path
config_file     = Path('UseCase_Pantheon/PantheonData/config.yml')
out_name        = Path('UseCase_Pantheon/PantheonData/metrics.csv')
plot_path       = Path('plots/Pantheon')

# Inputs
metric_delay = {'name':'One-way delay',
                'unit': 'ms',
                'measure':95,
                'bounds':[0,100], # expected value range
                'tag':'delay'     # do not change the tag
               }
convergence = {'expected': True,
               'confidence': 95,  # in %
               'tolerance': 5,    # in %
              }

# Compute/load the metrics
metrics = pantheon.compute_metric(result_dir_list, 
                                  meta_data_file, 
                                  convergence,
                                  [metric_delay],
                                  out_name = out_name)
data_file = str(result_dir_list[0] / 'fillp_datalink_delay_run1_flow1.csv')
plot_filename = "plot_example_metric.pdf"
custom_layout = {
    "title":None,
    "width":500,
    "height":300,
    "margin":dict(l=55, r=5, t=0, b=45),
    "legend":{'x':.1, 'y':.1},
    "xaxis":{'title':{'font':{'size':16},
                      'text':'Time [ s ]'}
            },
    "yaxis":{'title':{'font':{'size':16},
                      'text':metric_delay['name'] +' [ '+ metric_delay['unit'] +' ]'}
            }, 
}
triscale.analysis_metric(  data_file,
                           metric_delay,
                           plot=True,
                           plot_out_name=str(plot_path / plot_filename),
                           custom_layout = custom_layout,
                           convergence=convergence);

Output retrieved from file. Skipping computation.


> **Figure 3 (a)** Raw data (one-way delay) and metric data (95th percentile). _Example run of FillP._

[Back to top](#TriScale-Interactive-Plots)

### Figure 3b

In [7]:
# Construct the path to the different test results
result_dir_path = Path('UseCase_Pantheon/PantheonData/10runs_30s')
result_dir_list = [x for x in result_dir_path.iterdir() if x.is_dir()]
# Meta data file name
meta_data_file  = 'pantheon_metadata.json'
# Config file name and path
config_file     = Path('UseCase_Pantheon/PantheonData/config.yml')
out_name        = Path('UseCase_Pantheon/PantheonData/metrics.csv')
plot_path       = Path('plots/Pantheon')

# Inputs
metric_delay = {'name':'One-way delay',
                'unit': 'ms',
                'measure':95,
                'bounds':[0,100], # expected value range
                'tag':'delay'     # do not change the tag
               }
convergence = {'expected': True,
               'confidence': 95,  # in %
               'tolerance': 5,    # in %
              }
KPI_delay = {'percentile': 75,
             'confidence': 75,
             'name': 'One-way delay',
             'unit': 'ms',
             'bounds':[0,100],    # expected value range
             'tag':'delay'        # do not change the tag
            }

# Compute/load the metrics
metrics = pantheon.compute_metric(result_dir_list, 
                                  meta_data_file, 
                                  convergence,
                                  [metric_delay,metric_delay],
                                  out_name = out_name)
plot_out_name = "plot_example_KPI.pdf"

metric_data = np.array(metrics.loc[(metrics['cc'] == 'fillp') &
                          (metrics['datetime'] == result_dir_list[1].stem)].delay_value)

note = go.layout.Annotation(
        x=0.5,
        y=0,
        xref="paper",
        yref="y",
        text="KPI: 72.38 ms",
        showarrow=False,
        font={'size':16 }
    )
custom_layout = {
    "title":None,
    "width":300,
    "height":100,
    "margin":dict(l=0, r=0, t=5, b=40),
    "showlegend": False,
    "yaxis":{'title':{'font':{'size':16}},
#              'visible' : True
            },
    "xaxis":{'title':{'font':{'size':16},
                      'text':'95th percentile of one-way delay [ms]'}
            },
    "annotations":[note]
}
triscale.analysis_kpi(metric_data,
                    KPI_delay,
                    to_plot=['horizontal'],
                    plot_out_name=str(plot_path/plot_out_name),
                    custom_layout=custom_layout);

Output retrieved from file. Skipping computation.


> **Figure 3 (b)** Runs metric data and corresponding KPI value.

[Back to top](#TriScale-Interactive-Plots)

### Figure 3c

In [9]:
KPI_tput  = {'percentile': 25,
             'confidence': 75,
             'name': 'Average Throughput',
             'unit': 'Mbit/s',
             'bounds':[0,120],    # expected value range
             'tag':'throughput'   # do not change the tag
            }
KPI_delay = {'percentile': 75,
             'confidence': 75,
             'name': 'One-way delay',
             'unit': 'ms',
             'bounds':[0,100],    # expected value range
             'tag':'delay'        # do not change the tag
            }
score_delay = {'percentile': 75,
             'confidence': 75,
             'name': '95th perc. of One-way delay',
             'unit': 'ms',
             'tag':'delay'        # do not change the tag
            }
# Compute the KPIs
kpis = pantheon.compute_kpi(metrics,
                            [KPI_tput, KPI_delay],
                            'datetime',
                            plot=False,
                            verbose=False)
plot_path       = Path('plots/Pantheon')
plot_out_name = "plot_example_var_score.pdf"

kpi_data = np.array(kpis.loc[(kpis['cc'] == 'fillp')].delay_value)

note = go.layout.Annotation(
        x=0.5,
        y=0,
        xref="paper",
        yref="y",
        text="Var. Score: 1.66 ms",
        showarrow=False,
        font={'size':16 }
    )
custom_layout = {
    "title":None,
    "width":300,
    "height":100,
    "margin":dict(l=0, r=0, t=5, b=40),
    "showlegend": False,
#     "legend":{'x':.1, 'y':.1},
#     "xaxis":{'title':{'font':{'size':16},
#                       'text':'Time [ s ]'}
#             },
    "yaxis":{'title':{'font':{'size':16}},
#                       'text':'Time [ s ]'},
#              'visible' : True
            },
    "xaxis":{'title':{'font':{'size':16},
                      'text':'One-way delay KPIs [ms]'}
            },
    "annotations":[note]

}
triscale.analysis_variability(kpi_data,
                    score_delay,
                    to_plot=['horizontal'],
                    plot_out_name=str(plot_path/plot_out_name),
                    custom_layout=custom_layout);

> **Figure 3 (c)** Series KPI data and corresponding variability score.

[Back to top](#TriScale-Interactive-Plots)

### Figure 4

In [10]:
metric_tput = {'name':'Avg. Throughput',
               'unit': 'Mbit/s',
               'measure':50,
               'bounds':[0,120],  # expected value range
               'tag':'throughput' # do not change the tag
              }
convergence = {'expected': True,
               'confidence': 95,  # in %
               'tolerance': 5,    # in %
              }
result_dir_path = Path('UseCase_Pantheon/PantheonData/10_20_30_40_50_60s')
result_dir_list = [x for x in result_dir_path.iterdir() if x.is_dir()]
meta_data_file  = 'pantheon_metadata.json'
plot_path       = Path('plots/Pantheon')
sample = {'cc':'ledbat',
          'run':1}

custom_layout = {
    'title':None,
    "width":500,
    "height":300,
    "margin":dict(l=40, r=0, t=0, b=40),
    "legend":{'x':.1, 'y':.9,'font':{'size':18}},
    "xaxis":{'title':{'font':{'size':20},
                      'text':'Time [ s ]'}
            },
    "yaxis":{'title':{'font':{'size':20},
                      'text':metric_tput['name'] +' [ '+ metric_tput['unit'] +' ]'}
            }, 
}

runtimes = [10,60,20,50,40,30]
for i in [0,2,5,4,3,1]:
    if i != 0:
        custom_layout.update({"showlegend":False})
    plot_out_name = "plot_ledbat_%s_runtime.pdf" % runtimes[i]
    metrics_design, figure = pantheon.compute_metric( [result_dir_list[i]], 
                                          meta_data_file, 
                                          convergence,
                                          [metric_tput],
                                          plot=True,
                                          showplot=False,
                                          layout=custom_layout,
                                          plot_out_name=str(plot_path/plot_out_name),
                                          verbose=False,
                                          sample=sample)
    figure.show()

> **Figure 4** ...

[Back to top](#TriScale-Interactive-Plots)

### Figure 5

In [11]:
result_dir_path = Path('UseCase_Pantheon/PantheonData/10runs_30s')
result_dir_list = [x for x in result_dir_path.iterdir() if x.is_dir()]
meta_data_file  = 'pantheon_metadata.json'
config_file     = Path('UseCase_Pantheon/PantheonData/config.yml')
convergence = {'expected': True,
               'confidence': 95,  # in %
               'tolerance': 5,    # in %
              }
metric_tput = {'name':'Average Throughput',
               'unit': 'MBit/s',
               'measure':50,
               'bounds':[0,120],  # expected value range
               'tag':'throughput' # do not change the tag
              }
metric_delay = {'name':'95th perc. of One-way delay',
                'unit': 'ms',
                'measure':95,
                'bounds':[0,100], # expected value range
                'tag':'delay'     # do not change the tag
               }
metric_list = [metric_tput, metric_delay]
out_name = Path('UseCase_Pantheon/PantheonData/metrics.csv')
plot_path       = Path('plots/Pantheon')
metrics = pantheon.compute_metric(result_dir_list, 
                                  meta_data_file, 
                                  convergence,
                                  metric_list,
                                  out_name=out_name,
                                  force_computation=False,
                                  plot=False,
                                  verbose=False)

custom_layout = {
    'title':None,
    "width":400,
    "height":150,
    "margin":dict(l=25, r=0, t=0, b=0),
    "legend":{'x':.9, 'y':1.2,'font':{'size':16}},
    "xaxis" :None
}

# Passed test
plot_out_name = "plot_webrtc_autocorr_passed.pdf"
sample = metrics.loc[(metrics['cc'] == 'webrtc') & (metrics['datetime'] == '2019-08-22T07:59:10:+0200')]
plot_passed = triplots.autocorr_plot( sample.throughput_value.values,
                                      layout=custom_layout,
                                      out_name=str(plot_path/plot_out_name))
# # Failed test
plot_out_name = "plot_webrtc_autocorr_failed.pdf"
custom_layout.update({
    'showlegend':False,
    "xaxis":{'title':{'font':{'size':16},
                      'text':'Lag'}},
    "margin":dict(l=25, r=0, t=0, b=40)})
sample = metrics.loc[(metrics['cc'] == 'webrtc') & (metrics['datetime'] == '2019-08-21T12:14:13:+0200')]
plot_failed = triplots.autocorr_plot( sample.throughput_value.values,
                                      layout=custom_layout,
                                      out_name=str(plot_path/plot_out_name))
                                     


Output retrieved from file. Skipping computation.


> **Figure 5** ...

[Back to top](#TriScale-Interactive-Plots)

### Figure 6

In [12]:
result_dir_path = Path('UseCase_Pantheon/PantheonData/10runs_30s')
result_dir_list = [x for x in result_dir_path.iterdir() if x.is_dir()]
meta_data_file  = 'pantheon_metadata.json'
config_file     = Path('UseCase_Pantheon/PantheonData/config.yml')
convergence = {'expected': True,
               'confidence': 95,  # in %
               'tolerance': 5,    # in %
              }
metric_tput = {'name':'Average Throughput',
               'unit': 'MBit/s',
               'measure':50,
               'bounds':[0,120],  # expected value range
               'tag':'throughput' # do not change the tag
              }
metric_delay = {'name':'95th perc. of One-way delay',
                'unit': 'ms',
                'measure':95,
                'bounds':[0,100], # expected value range
                'tag':'delay'     # do not change the tag
               }
KPI_tput  = {'percentile': 25,
             'confidence': 75,
             'name': 'Average Throughput',
             'unit': 'MBit/s',
             'bounds':[0,120],    # expected value range
             'tag':'throughput'   # do not change the tag
            }
KPI_delay = {'percentile': 75,
             'confidence': 75,
             'name': '95th perc. of One-way delay',
             'unit': 'ms',
             'bounds':[0,100],    # expected value range
             'tag':'delay'        # do not change the tag
            }
score_tput  = {'percentile': 75,
             'confidence': 75,
             'name': 'Throughput',
             'unit': 'MBit/s',
             'tag':'throughput'   # do not change the tag
            }
score_delay = {'percentile': 75,
             'confidence': 75,
             'name': 'One-way delay',
             'unit': 'ms',
             'tag':'delay'        # do not change the tag
            }
out_name = Path('UseCase_Pantheon/PantheonData/metrics.csv')
plot_path       = Path('plots/Pantheon')

metric_list = [metric_tput, metric_delay]
kpi_list = [ KPI_tput, KPI_delay ]
score_list = [ score_tput, score_delay ]

metrics = pantheon.compute_metric(result_dir_list, 
                                  meta_data_file, 
                                  convergence,
                                  metric_list,
                                  out_name=out_name,
                                  force_computation=False,
                                  plot=False,
                                  verbose=False)
KPIs = pantheon.compute_kpi(metrics,
                            kpi_list,
                            series='datetime',
                            plot=False,
                            verbose=False)
scores = pantheon.compute_score(KPIs,
                            score_list,
                            plot=False,
                            verbose=False)


custom_layout = {
    "width":1000,
    "height":150,
    "margin":dict(l=30, r=40, t=25, b=45),
#     "legend":{'x':.9, 'y':1.2,'font':{'size':16}},
#     "xaxis" :None
}
plot_out_name = "plot_score_matrix.pdf"

pantheon.plot_triscale_scores_matrix( scores,
                                      score_list,
                                      config_file,
                                      layout = custom_layout,
                                      out_name=str(plot_path/plot_out_name)
                                    )
                                     


Output retrieved from file. Skipping computation.


> **Figure 6** ...

[Back to top](#TriScale-Interactive-Plots)

---

In [ ]:
# Necessary import

from pathlib import Path

import numpy as np

import triscale
import UseCase_Pantheon.pantheon as pantheon

%load_ext autoreload
%autoreload 2

In [ ]:
# Define the paths to files

data_path = Path('')
data_path = data_path / 'UseCase_Pantheon' / 'PantheonData' / '10runs_30s' / '2019-08-20T15:34:33:+0200'

plot_path = Path('')
plot_path = plot_path / 'plots' / 'Pantheon'

perf_file = data_path / 'pantheon_perf.json'

meta_file = data_path / 'pantheon_metadata.json'

config_file = Path('')
config_file = config_file / 'UseCase_Pantheon' / 'PantheonData' / 'config.yml'

In [ ]:
# Compute Pantheon KPI using TriScale's Analysis module

# The KPI side is left undefined here
# -> compute_KPI() adjusts it based on the metric
# throughput : lower-bound
# delay :      upper-bound
KPI={ 'percentile': 50,
      'confidence': 95,
      'class': 'one-sided',
      'side': None} 
perf_KPI = pantheon.compute_KPI(str(perf_file), KPI, verbose=False)

## Figure 2

In [ ]:
# Generate the "full" plots
custom_layout = {
    "title":None,
    "width":450,
    "height":500,
    "showlegend":False,
}

# Plot it
pantheon.plot_KPI(perf_KPI, 
                  meta_file, 
                  config_file,
                  layout=custom_layout, 
                  out_name=str(plot_path / "plot_summary_triscale.pdf"),
                  show=False)
# Compare to the original Pantheon plots
pantheon.plot_summary(perf_file, 
                      meta_file, 
                      config_file, 
                      layout=custom_layout,
                      out_name=str(plot_path / "plot_summary_pantheon.pdf"),
                      show=True);

In [ ]:
# Generate the "zoom-in" plots
custom_layout = {
    "title":None,
    "width":450,
    "height":500,
    "xaxis":{'range':[76,42],
             'autorange':False,
             'title':{'font':{'size':16}}
            },
    "yaxis":{'range':[55,115],
             'title':{'font':{'size':16}}
            },
    "showlegend":False,
}

# Plot it
pantheon.plot_KPI(perf_KPI, 
                  meta_file, 
                  config_file, 
                  layout=custom_layout, 
                  out_name=str(plot_path / "plot_zoom_triscale.pdf"),
                  show=True)
# Compare to the original Pantheon plots
pantheon.plot_summary(perf_file, 
                      meta_file, 
                      config_file, 
                      layout=custom_layout, 
                      out_name=str(plot_path / "plot_zoom_pantheon.pdf"),
                      show=True);

## Figure 3

In [ ]:
# Code generating the figure
# ...


> Data analysis and visualization reproduced from [[66]](). The dots represent the mean performance of the runs; the ellipses represent the $(1-\sigma)$ variation across runs.

[Back to top](#TriScale-Interactive-Plots)